# Test for GraphSparqlQAChain

Following tutorial at <https://python.langchain.com/docs/integrations/graphs/rdflib_sparql/>.

In [ ]:
# from langchain_openai import ChatOpenAI
from langchain_ollama.llms import OllamaLLM
from langchain.prompts import PromptTemplate
from langchain.chains import GraphSparqlQAChain
from langchain_community.graphs import RdfGraph
from dotenv import load_dotenv
load_dotenv()

## Initialize the Graph

In [ ]:
# Initialize the RDF graph
graph = RdfGraph(
    standard="rdf",
    serialization="ttl",
    source_file="data/graph.ttl"
)

In [ ]:
# Get the schema from the graph
schema = graph.load_schema()

In [ ]:
# Create the template for constructing the SPARQL select query
sparql_select_prompt=PromptTemplate(
    input_variables=["prompt", "schema"],
    template="""
    You are an expert in SPARQL queries and RDF graph structures. Your task is to generate a SPARQL query based on the provided schema and the user's question.
    Use only the node types and properties provided in the schema.
    Do not use any node types or properties not explicitly listed.
    Include all necessary PREFIX declarations.
    Return only the SPARQL query. Do not include any text before or after the query. Do not use triple backticks or any markdown formatting.
    Your RDF graph has these prefixes, classes, and properties:

    @prefix coptic: <http://www.semanticweb.org/sjhuskey/ontologies/2025/7/coptic-metadata-viewer/> .
    @prefix dcmitype: <http://purl.org/dc/dcmitype/> .
    @prefix dcterms: <http://purl.org/dc/terms/> .
    @prefix foaf: <http://xmlns.com/foaf/0.1/> .
    @prefix frbr: <http://purl.org/vocab/frbr/core#> .
    @prefix lawd: <http://lawd.info/ontology/> .
    @prefix ns1: <http://lexinfo.net/ontology/2.0/lexinfo#> .
    @prefix owl: <http://www.w3.org/2002/07/owl#> .
    @prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
    @prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
    @prefix schema1: <http://schema.org/> .
    @prefix skos: <http://www.w3.org/2004/02/skos/core#> .
    @prefix time: <http://www.w3.org/2006/time#> .
    
    - coptic:Colophon:
      - dcterms:description
      - dcterms:identifier
      - dcterms:isPartOf
      - dcterms:references
      - dcterms:type
      - ns1:translation
      - rdf:type
      - time:hasBeginning
      - time:hasEnd

    - coptic:Title:
      - dcterms:description
      - dcterms:identifier
      - dcterms:isPartOf
      - dcterms:references
      - dcterms:type
      - rdf:type

    - dcmitype:Collection:
      - dcterms:hasPart
      - dcterms:identifier
      - dcterms:spatial
      - rdf:type

    - dcterms:Agent:
      - dcterms:creator
      - dcterms:description
      - dcterms:identifier
      - foaf:name
      - owl:sameAs
      - rdf:type
      - schema1:title

    - dcterms:PhysicalResource:
      - dcterms:bibliographicCitation
      - dcterms:description
      - dcterms:hasPart
      - dcterms:identifier
      - dcterms:isPartOf
      - dcterms:medium
      - rdf:type
      - time:hasBeginning
      - time:hasEnd

    - foaf:Person:
      - dcterms:identifier
      - dcterms:isReferencedBy
      - foaf:name
      - ns1:transliteration
      - rdf:type
      - rdfs:label
      - schema1:birthPlace
      - schema1:gender
      - schema1:roleName
      - time:hasBeginning
      - time:hasEnd

    - frbr:Work:
      - dcterms:creator
      - dcterms:description
      - dcterms:identifier
      - dcterms:isPartOf
      - dcterms:isReferencedBy
      - dcterms:temporal
      - dcterms:title
      - rdf:type
      - rdfs:label

    - lawd:Place:
      - lawd:primaryForm
      - rdf:type
      - rdfs:label
      - skos:exactMatch

    Do not use any node types and properties that are not explicitly provided.
    Include all necessary prefixes.
    Always return a human-readable label instead of a URI when possible.
    When using UNION, wrap all query patterns inside a single outer WHERE clause.
    Do not use multiple WHERE clauses.
    \n\nThe question is:\n{prompt}
    Schema: {schema}
    """)

# Create the template for the question-answering prompt
qa_prompt = PromptTemplate(
    input_variables=["context", "prompt"],
    template="""
You are a friendly and knowledgeable digital research assistant specializing in Coptic and Greek texts.

Given the structured data below, answer the user’s question in clear, natural language.
Use complete sentences. If multilingual forms are included, identify which language each form belongs to.

Structured data:
{context}

User question:
{prompt}

Answer:
"""
)

In [ ]:
# Initialize the GraphSparqlQAChain with the LLM, prompts, and graph
chain = GraphSparqlQAChain.from_llm(
    # ChatOpenAI(model="gpt-4o-mini", temperature=0),
    OllamaLLM(model="mistral-small3.2", temperature=0),
    sparql_select_prompt=sparql_select_prompt,
    qa_prompt=qa_prompt,
    graph=graph,
    verbose=True,
    return_intermediate_steps=True,
    allow_dangerous_requests=True
)

In [10]:
# Example query to test the chain
output = chain.invoke("Who is the creator of the work with the title 'Sermo asceticus?'")  # Example query
print(output['result'])  # Print the answer



> Entering new GraphSparqlQAChain chain...
Identified intent:
SELECT
Generated SPARQL:
PREFIX dcterms: <http://purl.org/dc/terms/>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX frbr: <http://purl.org/vocab/frbr/core#>
PREFIX foaf: <http://xmlns.com/foaf/0.1/>
PREFIX schema1: <http://schema.org/>

SELECT ?creatorName WHERE {
  ?work rdf:type frbr:Work ;
        dcterms:title "Sermo asceticus" ;
        dcterms:creator ?creator .
  ?creator foaf:name ?creatorName .
}
Full Context:
[(rdflib.term.Literal('Stephen of Thebes'),), (rdflib.term.Literal('ⲥⲧⲉⲫⲁⲛⲟⲥ', lang='cop'),), (rdflib.term.Literal('Στέφανος', lang='el'),)]

> Finished chain.
Based on the structured data provided, the creator of the work titled "Sermo asceticus" is Stephen of Thebes. This name appears in three forms:

- English: Stephen of Thebes
- Coptic: ⲥⲧⲉⲫⲁⲛⲟⲥ
- Greek: Στέφανος

Stephen of Thebes is the individual associated with this work.


In [11]:
output = chain.invoke("What is known about the 'Encomium of Theodore Archbishop of Antioch")  # Example query
print(output['result'])  # Print the answer



> Entering new GraphSparqlQAChain chain...
Identified intent:
SELECT
Generated SPARQL:
PREFIX dcmitype: <http://purl.org/dc/dcmitype/>
PREFIX dcterms: <http://purl.org/dc/terms/>
PREFIX foaf: <http://xmlns.com/foaf/0.1/>
PREFIX frbr: <http://purl.org/vocab/frbr/core#>
PREFIX lawd: <http://lawd.info/ontology/>
PREFIX ns1: <http://lexinfo.net/ontology/2.0/lexinfo#>
PREFIX owl: <http://www.w3.org/2002/07/owl#>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX schema1: <http://schema.org/>
PREFIX skos: <http://www.w3.org/2004/02/skos/core#>
PREFIX time: <http://www.w3.org/2006/time#>

SELECT DISTINCT ?label ?description ?creatorName ?creatorRole ?temporal ?spatial ?medium ?type ?references ?isReferencedBy ?bibliographicCitation ?hasPart ?isPartOf ?extent ?publisher ?issued ?hasBeginning ?hasEnd ?transliteration ?translation ?sameAs ?birthPlace ?gender ?roleName WHERE {
  {
    ?work rdf:type frbr:Work .
    ?work dcterms

In [16]:
output = chain.invoke("What is in the graph about Theodore the Anatolian?")  # Example query
print(output['result'])  # Print the answer



> Entering new GraphSparqlQAChain chain...
Identified intent:
SELECT
Generated SPARQL:
PREFIX dcterms: <http://purl.org/dc/terms/>
PREFIX foaf: <http://xmlns.com/foaf/0.1/>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX schema1: <http://schema.org/>
PREFIX ns1: <http://lexinfo.net/ontology/2.0/lexinfo#>
PREFIX time: <http://www.w3.org/2006/time#>
PREFIX lawd: <http://lawd.info/ontology/>
PREFIX skos: <http://www.w3.org/2004/02/skos/core#>
PREFIX owl: <http://www.w3.org/2002/07/owl#>
PREFIX frbr: <http://purl.org/vocab/frbr/core#>
PREFIX dcmitype: <http://purl.org/dc/dcmitype/>

SELECT ?person ?name ?description ?roleName ?birthPlace ?gender ?title WHERE {
  ?person rdf:type foaf:Person .
  ?person foaf:name ?name .
  FILTER(CONTAINS(LCASE(?name), "theodore the anatolian"))
  OPTIONAL { ?person dcterms:description ?description . }
  OPTIONAL { ?person schema1:roleName ?roleName . }
  OPTIONAL { ?person schema1:birt

In [12]:
output = chain.invoke("Please find any text in the graph with the string 'Theodore the Anatolian'.")  # Example query
print(output['result'])  # Print the answer



> Entering new GraphSparqlQAChain chain...
Identified intent:
SELECT
Generated SPARQL:
PREFIX dcmitype: <http://purl.org/dc/dcmitype/>
PREFIX dcterms: <http://purl.org/dc/terms/>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX foaf: <http://xmlns.com/foaf/0.1/>
PREFIX frbr: <http://purl.org/vocab/frbr/core#>
PREFIX lawd: <http://lawd.info/ontology/>
PREFIX ns1: <http://lexinfo.net/ontology/2.0/lexinfo#>
PREFIX owl: <http://www.w3.org/2002/07/owl#>
PREFIX schema1: <http://schema.org/>
PREFIX skos: <http://www.w3.org/2004/02/skos/core#>
PREFIX time: <http://www.w3.org/2006/time#>

SELECT ?text ?textDescription WHERE {
  {
    ?text rdf:type dcmitype:Text .
    ?text dcterms:description ?textDescription .
    FILTER(CONTAINS(STR(?textDescription), "Theodore the Anatolian"))
  }
  UNION
  {
    ?text rdf:type dcmitype:Text .
    ?text rdf:value ?textValue .
    FILTER(CONTAINS(STR(?textValue), "Theodore the Anatolian")

In [41]:
output = chain.invoke("Tell me more about title 307")  # Example query
print(output['result'])  # Print the answer



> Entering new GraphSparqlQAChain chain...
Identified intent:
SELECT
Generated SPARQL:
PREFIX dcterms: <http://purl.org/dc/terms/>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX frbr: <http://purl.org/vocab/frbr/core#>
PREFIX foaf: <http://xmlns.com/foaf/0.1/>
PREFIX schema: <http://schema.org/>
PREFIX lawd: <http://lawd.info/ontology/>
PREFIX time: <http://www.w3.org/2006/time#>
PREFIX ns1: <http://lexinfo.net/ontology/2.0/lexinfo#>
PREFIX owl: <http://www.w3.org/2002/07/owl#>
PREFIX skos: <http://www.w3.org/2004/02/skos/core#>

SELECT ?work ?title ?description ?creatorName ?creatorRole ?creatorGender ?creatorBirthPlace ?temporal ?references ?isReferencedBy ?hasPart ?isPartOf ?medium ?extent ?issued ?publisher ?bibliographicCitation ?spatial ?type ?hasBeginning ?hasEnd WHERE {
  {
    ?work dcterms:title "307" .
    OPTIONAL { ?work dcterms:description ?description . }
    OPTIONAL { ?work dcterms:creator ?creato

In [ ]:
output = chain.invoke("Tell me more about the title with identifier 307")  # Example query
print(output['result'])  # Print the answer



> Entering new GraphSparqlQAChain chain...
Identified intent:
SELECT
Generated SPARQL:
PREFIX dcmitype: <http://purl.org/dc/dcmitype/>
PREFIX dcterms: <http://purl.org/dc/terms/>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX frbr: <http://purl.org/vocab/frbr/core#>
PREFIX foaf: <http://xmlns.com/foaf/0.1/>
PREFIX lawd: <http://lawd.info/ontology/>
PREFIX time: <http://www.w3.org/2006/time#>
PREFIX ns1: <http://lexinfo.net/ontology/2.0/lexinfo#>
PREFIX schema1: <http://schema.org/>

SELECT ?title ?description ?creatorName ?creatorRole ?creatorGender ?creatorBirthPlace ?issued ?temporal ?spatial ?medium ?extent ?bibliographicCitation ?references ?type ?isPartOf ?hasPart ?translation ?transliteration WHERE {
  {
    ?titleNode rdf:type dcmitype:Text .
    ?titleNode dcterms:identifier "307" .
    OPTIONAL { ?titleNode dcterms:title ?title . }
    OPTIONAL { ?titleNode dcterms:description ?description . }
    OPTIONA

In [8]:
output = chain.invoke("Which manuscript dcterms:hasPart the title with id 307?")  # Example query
print(output['result'])  # Print the answer



> Entering new GraphSparqlQAChain chain...
Identified intent:
SELECT
Generated SPARQL:
PREFIX dcterms: <http://purl.org/dc/terms/>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX lawd: <http://lawd.info/ontology/>
PREFIX foaf: <http://xmlns.com/foaf/0.1/>
PREFIX schema1: <http://schema.org/>
PREFIX ns1: <http://lexinfo.net/ontology/2.0/lexinfo#>
PREFIX time: <http://www.w3.org/2006/time#>
PREFIX owl: <http://www.w2.org/2002/07/owl#>
PREFIX skos: <http://www.w3.org/2004/02/skos/core#>
PREFIX frbr: <http://purl.org/vocab/frbr/core#>

SELECT ?manuscript ?titleLabel WHERE {
  ?manuscript rdf:type dcterms:PhysicalResource .
  ?manuscript dcterms:hasPart ?part .
  ?part dcterms:identifier "307" .
  ?part dcterms:title ?title .
  ?title rdfs:label ?titleLabel .
}
Full Context:
[]

> Finished chain.
I am not able to respond to that question. Please be more specific.
